In [1]:
# from transformers import AutoTokenizer, AutoModel
import numpy as np
# from sklearn.metrics.pairwise import cosine_similarity
import torch
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
# from nltk.stem import WordNetLemmatizer
# import pymorphy2
import string

In [2]:
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to /home/vera/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/vera/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

# Sentence Transformers

In [3]:
# !pip install sentence_transformers

In [4]:
# !pip install faiss-cpu

In [5]:
stop_words = set(stopwords.words('russian'))
# lemmatizer = WordNetLemmatizer()

In [6]:
from sentence_transformers import SentenceTransformer, util
import faiss

In [7]:
data = pd.read_csv('merged_file.csv')

In [9]:
data['description'] = data['description'].astype(str)

In [10]:
data['annotation_len'] = data['description'].apply(lambda x: len(str(x).split()) if pd.notnull(x) else 0)
data = data[data['annotation_len'] > 10] # Отсечение слишком коротких аннотаций

In [11]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 6809 entries, 0 to 6887
Data columns (total 12 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   page_url          6809 non-null   object 
 1   image_url         6809 non-null   object 
 2   tvshow_title      6809 non-null   object 
 3   description       6809 non-null   object 
 4   names             5456 non-null   object 
 5   names_and_roles   5456 non-null   object 
 6   genre             6613 non-null   object 
 7   dates             6809 non-null   object 
 8   country           6808 non-null   object 
 9   imdb              6298 non-null   float64
 10  kinopoisk_rating  6003 non-null   float64
 11  annotation_len    6809 non-null   int64  
dtypes: float64(2), int64(1), object(9)
memory usage: 691.5+ KB


In [12]:
data.head()

page_url  \
0   https://myshows.me/view/7718/   
1  https://myshows.me/view/11945/   
2      https://myshows.me/view/2/   
3     https://myshows.me/view/45/   
4    https://myshows.me/view/304/   

                                           image_url            tvshow_title  \
0  https://media.myshows.me/shows/1920/9/49/9492c...                  Шерлок   
1  https://media.myshows.me/shows/1920/d/d1/dd10e...          Игра престолов   
2  https://media.myshows.me/shows/1920/2/a9/2a932...  Теория большого взрыва   
3  https://media.myshows.me/shows/1920/f/c3/fc37c...      Сверхъестественное   
4  https://media.myshows.me/shows/1920/1/23/12314...                 Отбросы   

                                         description  \
0  История о Шерлоке Холмсе и докторе Ватсоне в Л...   
1  Игра Престолов — американский фэнтези-сериал, ...   
2  Теория большого взрыва это, уже ставший класси...   
3  Больше десяти лет назад это шоу начиналось, ка...   
4  Компания мелких подонков старшего школьного во...   

                                               names  \
0               Benedict Cumberbatch, Martin Freeman   
1  Peter Dinklage, Kit Harington, Lena Headey, Em...   
2  Johnny Galecki, Jim Parsons, Simon Helberg, Ku...   
3  Jared Padalecki, Jensen Ackles, Misha Collins,...   
4  Nathan Stewart-Jarrett, Joseph Gilgun, Antonia...   

                                     names_and_roles  \
0  Benedict Cumberbatch (Sherlock Holmes), Martin...   
1  Peter Dinklage (Tyrion Lannister), Kit Haringt...   
2  Johnny Galecki (Leonard Leakey Hofstadter), Ji...   
3  Jared Padalecki (Sam Winchester), Jensen Ackle...   
4  Nathan Stewart-Jarrett (Curtis Donovan), Josep...   

                               genre                    dates         country  \
0          Криминал, Драма, Детектив  25.07.2010 — 15.01.2017  Великобритания   
1        Приключения, Драма, Фэнтези  17.04.2011 — 26.05.2019             США   
2                            Комедия  24.09.2007 — 27.12.2019             США   
3  Боевик, Драма, Сверхъестественное  13.09.2005 — 19.11.2020             США   
4         Комедия, Драма, Фантастика  12.11.2009 — 11.12.2013  Великобритания   

   imdb  kinopoisk_rating  annotation_len  
0   9.1             8.856             143  
1   9.2             8.981              35  
2   8.1             8.627             227  
3   8.4             8.237             174  
4   8.2             8.062             179

In [15]:
def clean_text(text):
    text = re.sub(r'\r\n', ' ', text)
    text = text.replace('\xa0', ' ')
    clean_pattern = re.compile(r'[^a-zA-Zа-яА-ЯёЁ0-9.,!?;:\s]')
    text = clean_pattern.sub('', text)
    url_pattern = re.compile(r'http\S+|www\S+|https\S+')
    text = url_pattern.sub(r'', text)
    text = text.translate(str.maketrans('', '', string.punctuation))
    text = text.lower()
    return text

data['clean_description'] = data['description'].apply(clean_text)

/tmp/ipykernel_66816/1946767519.py:13: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['clean_description'] = data['description'].apply(clean_text)


In [17]:
from sklearn.decomposition import TruncatedSVD
from sklearn.decomposition import FastICA

In [19]:
data['names_and_roles'] = data['names_and_roles'].fillna('Не указаны')

/tmp/ipykernel_66816/1587781095.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['names_and_roles'] = data['names_and_roles'].fillna('Не указаны')


In [20]:
data['genre'] = data['genre'].fillna('Не указан')

/tmp/ipykernel_66816/1379828616.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['genre'] = data['genre'].fillna('Не указан')


In [21]:
# Шаг 2: Векторизация описаний сериалов с помощью Sentence Transformers
# Используем модель Sentence Transformers для асимметричного семантического поиска
model = SentenceTransformer('paraphrase-multilingual-mpnet-base-v2')  # all-mpnet-base-v2 #sentence-transformers/distiluse-base-multilingual-cased-v1
# model = SentenceTransformer('sentence-transformers/distiluse-base-multilingual-cased-v1')
# model = SentenceTransformer('sentence-transformers/LaBSE')

# model = SentenceTransformer('sentence-transformers/paraphrase-multilingual-MiniLM-L12-v2')
model.to('cuda');
# descriptions = data['clean_description'].tolist()
# # description_embeddings = model.encode(descriptions, convert_to_tensor=True).cpu().numpy()

/home/vera/miniforge3/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [22]:
descriptions = data['clean_description'].tolist()
description_embeddings = model.encode(descriptions, convert_to_tensor=True)
# description_embeddings = description_embeddings / torch.norm(description_embeddings, dim=1, keepdim=True)  # Нормализация
description_embeddings = description_embeddings.cpu().numpy()

In [23]:
actors = data['names_and_roles'].tolist()
actors_embeddings = model.encode(actors, convert_to_tensor=True)
# actors_embeddings = actors_embeddings / torch.norm(actors_embeddings, dim=1, keepdim=True)  # Нормализация
actors_embeddings = actors_embeddings.cpu().numpy()

In [24]:
genre = data['genre'].tolist()
genre_embeddings = model.encode(genre, convert_to_tensor=True)
# genre_embeddings = genre_embeddings / torch.norm(genre_embeddings, dim=1, keepdim=True)  # Нормализация
genre_embeddings = genre_embeddings.cpu().numpy()

In [25]:
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import Normalizer

In [26]:
description_weight = 0.7
actors_weight = 0.15
genre_weight = 0.15

In [27]:
weighted_description_embeddings = description_embeddings * description_weight
weighted_actors_embeddings = actors_embeddings * actors_weight
weighted_genre_embeddings = genre_embeddings * genre_weight

In [28]:
combined_embeddings = np.concatenate((weighted_description_embeddings, weighted_actors_embeddings, weighted_genre_embeddings), axis=1)

In [29]:
# ica = make_pipeline(FastICA(n_components=100, random_state=0), Normalizer(copy=False))
# description_embeddings = ica.fit_transform(description_embeddings)

In [30]:
lsa = make_pipeline(TruncatedSVD(n_components=100), Normalizer(copy=False))
combined_embeddings = lsa.fit_transform(combined_embeddings)
explained_variance = lsa[0].explained_variance_ratio_.sum()
print(f"Explained variance of the SVD step: {explained_variance * 100:.1f}%")

Explained variance of the SVD step: 82.7%


In [31]:
import joblib

In [32]:
joblib.dump(lsa, 'lsa_model.pkl')

['lsa_model.pkl']

In [33]:
# Нормализация векторов для косинусного сходства
combined_embeddings = combined_embeddings / np.linalg.norm(combined_embeddings, axis=1, keepdims=True)

In [34]:
# Создание индекса с использованием Faiss для косинусного сходства
dimension = combined_embeddings.shape[1]
index = faiss.IndexFlatIP(dimension)
index.add(combined_embeddings)


In [37]:
# Обработка пользовательского запроса
def search_series(user_query, top_k=10):
    user_query = clean_text(user_query)
    query_embedding = model.encode([user_query], convert_to_tensor=True).cpu().numpy()
    weighted_query_embedding = np.concatenate((query_embedding * description_weight,
                                               query_embedding * actors_weight,
                                               query_embedding * genre_weight), axis=1)
    weighted_query_embedding = lsa.transform(weighted_query_embedding)
    weighted_query_embedding = weighted_query_embedding / np.linalg.norm(weighted_query_embedding, axis=1, keepdims=True)  # Нормализация
    D, I = index.search(weighted_query_embedding, top_k)
    results = data.iloc[I[0]].copy()
    cosine_similarities = D[0]
    results['cosine_similarity'] = cosine_similarities
    return results

In [40]:
# Пример пользовательского запроса
user_query = "Молодые специалисты после школы пришли в больницу"
top_k_results = search_series(user_query)
top_k_results

#0.594781
#0.810437 - evclid

page_url  \
19       https://myshows.me/view/55/   
5804  https://myshows.me/view/64334/   
3271  https://myshows.me/view/65613/   
4097  https://myshows.me/view/20585/   
1837  https://myshows.me/view/27947/   
3476  https://myshows.me/view/25185/   
714   https://myshows.me/view/53657/   
4074  https://myshows.me/view/73498/   
5154   https://myshows.me/view/7676/   
3106  https://myshows.me/view/87793/   

                                              image_url  \
19    https://media.myshows.me/shows/1920/3/21/32187...   
5804  https://media.myshows.me/shows/1920/1/d9/1d949...   
3271  https://media.myshows.me/shows/1920/d/4d/d4da7...   
4097  https://media.myshows.me/shows/1920/a/68/a68d5...   
1837  https://media.myshows.me/shows/1920/2/c0/2c0b5...   
3476  https://media.myshows.me/shows/1920/2/fb/2fb9f...   
714   https://media.myshows.me/shows/1920/8/88/88898...   
4074  https://media.myshows.me/shows/1920/5/8b/58b02...   
5154  https://media.myshows.me/shows/1920/9/27/92798...   
3106  https://media.myshows.me/shows/1920/6/4f/64f65...   

                    tvshow_title  \
19                       Клиника   
5804                 Медперсонал   
3271          Врачебная мудрость   
4097                        Кома   
1837  Красные браслеты (Испания)   
3476          Доктор Эмили Оуэнс   
714                    Ординатор   
4074                  Подслушано   
5154             Дэцкая больница   
3106               Доктор Кризис   

                                            description  \
19    Отучившись четыре года в медицинской школе, Дж...   
5804  Сюжет сериала разворачивается в Торонто, где у...   
3271  Истории врачей и медсестёр, которые окончили о...   
4097  Молодая студентка-медик обнаруживает, что что-...   
1837  По воле злого рока несколько подростков попада...   
3476  Наконец-то Эмили Оуэнс чувствует, что повзросл...   
714   Молодой врач-ординатор Девон Правеш начинает к...   
4074  Пятеро друзей — Юра, Джулс, Лика, Крест и Кост...   
5154  Больница  не место для лентяев. Больница  эт...   
3106  Два гениальных доктора, которые в школе соперн...   

                                                  names  \
19    Donald Faison, John C. McGinley, Ken Jenkins, ...   
5804  Nicola Correia-Damude, Cathy White, Alexandra ...   
3271  Jo Jung Suk, Kim Dae Myung, Jung Kyung-Ho, Jun...   
4097  Lauren Ambrose, Natalie Knepp, Michael Weston,...   
1837  Marc Balaguer, Igor Szpakowski, Joana Vilapuig...   
3476  Mamie Gummer, Aja Naomi King, Justin Hartley, ...   
714   Matt Czuchry, Manish Dayal, Bruce Greenwood, M...   
4074  Александр Новиков, Валентина Ляпина, Никита Па...   
5154  Rob Huebel, Rob Corddry, Ken Marino, Erinn Hay...   
3106                                                NaN   

                                        names_and_roles  \
19    Donald Faison (Dr. Christopher Duncan Turk), J...   
5804  Nicola Correia-Damude (Dr. Vanessa Banks), Cat...   
3271  Jo Jung Suk (Ik Joon), Kim Dae Myung (Suk Hyun...   
4097  Lauren Ambrose (Susan Wheeler), Natalie Knepp ...   
1837  Marc Balaguer (Toni), Igor Szpakowski (Jordi),...   
3476  Mamie Gummer (Emily Owens), Aja Naomi King (Ca...   
714   Matt Czuchry (Dr. Conrad Hawkins), Manish Daya...   
4074  Александр Новиков (Юра), Валентина Ляпина (Джу...   
5154  Rob Huebel (Dr. Owen Maestro / Rob Huebel), Ro...   
3106                                         Не указаны   

                                genre                    dates      country  \
19        Комедия, Драма, Медицинский  02.10.2001 — 17.03.2010          США   
5804               Драма, Медицинский  06.01.2020 — 29.08.2021       Канада   
3271               Драма, Медицинский  12.03.2020 — 16.09.2021  Южная Корея   
4097      Детектив, Драма, Фантастика  03.09.2012 — 04.09.2012          США   
1837                            Драма  24.01.2011 — 22.04.2013      Испания   
3476        Комедия, Драма, Романтика  16.10.2012 — 05.02.2013          США   
714       Драма, Медицинский, Триллер

In [41]:
# Сохранение эмбеддингов
np.save('combined_embeddings_2.npy', description_embeddings)
# np.save('actors_embeddings_2.npy', actors_embeddings)
# np.save('genre_embeddings_2.npy', genre_embeddings)

# Сохранение FAISS индекса
faiss.write_index(index, 'faiss_index_2.bin')

# RuBERT - нужна другая предобработка

In [227]:
import torch
from transformers import AutoTokenizer, AutoModel
name = "cointegrated/rubert-tiny2"
tokenizer = AutoTokenizer.from_pretrained(name)
model = AutoModel.from_pretrained(name)

In [228]:
model = SentenceTransformer(name) # Используем RuBERT для семантического поиска
descriptions = data['description'].tolist()
description_embeddings = model.encode(descriptions, convert_to_tensor=True).cpu().numpy()

# Нормализация векторов для косинусного сходства
description_embeddings = description_embeddings / np.linalg.norm(description_embeddings, axis=1, keepdims=True)

# Создание индекса с использованием Faiss для косинусного сходства
dimension = description_embeddings.shape[1]
index = faiss.IndexFlatIP(dimension)
index.add(description_embeddings)


/home/vera/miniforge3/lib/python3.10/site-packages/huggingface_hub/file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [229]:
# Шаг 4: Обработка пользовательского запроса и асимметричный поиск
def search_series(user_query, top_k=10):
    # user_query = clean_text(user_query)
    user_query = (user_query)
    query_embedding = model.encode([user_query], convert_to_tensor=True).cpu().numpy()
    query_embedding = query_embedding / np.linalg.norm(query_embedding, axis=1, keepdims=True) # Нормализация
    D, I = index.search(query_embedding, top_k)
    results = data.iloc[I[0]].copy()
    cosine_similarities = D[0]
    results['cosine_similarity'] = cosine_similarities
    return results

# Пример пользовательского запроса
user_query = "Учитель, больной раком, варит метамфетамин, чтобы оставить своей семье денег"
top_k_results = search_series(user_query)
top_k_results

title                            link  \
7510        Клятва любви  https://myshows.me/view/74588/   
3182  Мэри убивает людей  https://myshows.me/view/51989/   
1851         Бесстыдники    https://myshows.me/view/810/   
4353       Раскосяченные  https://myshows.me/view/53374/   
2364               Кровь  https://myshows.me/view/42175/   
7320   Боб любит Абишолу  https://myshows.me/view/62313/   
4563        Пьяная фирма  https://myshows.me/view/51654/   
5446     Дэцкая больница   https://myshows.me/view/7676/   
2062           Санка Рэа  https://myshows.me/view/24059/   
1878         Алхимия душ  https://myshows.me/view/79093/   

                                            description  annotation_len  \
7510  отца линь чжисяо талантливой виолончелистки го...              33   
3182  доктор мэри харрис матьодиночка и врач скорой ...              55   
1851  жизнь детей из многодетной семьи оставленной м...              13   
4353  конопляная легенда рут уайтфезер фельдман нани...              27   
2364  пак джи сан красив богат умен заведующий отдел...              30   
7320  продавец носков из детройта боб пережил инфарк...              22   
4563  похмельный сериал про гениального врача которы...              16   
5446  больница  не место для лентяев больница  это м...              42   
2062  фуруя сын священника одержим зомби он коллекци...              53   
1878  чан ук  мужчина из респектабельной семьи котор...              23   

      cosine_similarity  
7510           0.709849  
3182           0.698886  
1851           0.698359  
4353           0.697979  
2364           0.696770  
7320           0.695213  
4563           0.695000  
5446           0.691805  
2062           0.688429  
1878           0.687544